# Flickr API  

![Flickr](https://www.flickrhelp.com/hc/article_attachments/4419907628308/unnamed__1_.png)  

Flickr provides access to download geotagged images through its API, which is relatively straightforward to use and imposes minimal restrictions for scraping images.  

A typical Flickr post can be viewed here: [link](https://www.flickr.com/photos/92959567@N00/227080829).  

The objective of this exercise is to create a table containing images from a specific area along with their associated information.  

To achieve this, we will use the "Python Flickr API" library to handle authentication. Once authenticated, you can utilize the methods detailed in the API documentation [here](https://www.flickr.com/services/api/).  

The API methods fall under different authentication levels, such as:  
- *Requires 'write' permission for authentication.*  
- *Requires 'read' permission for authentication.*  
- *Does not require authentication.*  

Focus only on the methods that do not require authentication and disregard those needing "write" or "read" permissions.

## Geo Search
### Preparation & First Searches
First, we pip install the library with `pip install flickrapi`.

Import the passwords: 

In [1]:
import sys
sys.path.append(r'E:\ucl\MyPythonModules')

import passwords as pw

api_key = "pw.flickr_key"
api_secret = "pw.flickr_secret"

print (api_key)
print (api_secret)

pw.flickr_key
pw.flickr_secret


Import the libraries we need. The code connects to the flickr api. The connection will be stored in an object called `flickr`.

In [2]:
pip install flickrapi

Note: you may need to restart the kernel to use updated packages.


In [3]:
pip install folium

Note: you may need to restart the kernel to use updated packages.


In [4]:
pip list | findstr flickrapi


flickrapi                 2.4.0
Note: you may need to restart the kernel to use updated packages.


In [5]:
import flickrapi
import pprint

api_key = "9348c02df6636b4aacdbddf3b0a15233"
api_secret = "9b94c1c6e76a24ef"

try:
    flickr = flickrapi.FlickrAPI(api_key, api_secret, format='parsed-json')
    response = flickr.test.echo()
    print("Flickr API 连接成功！")
    pprint.pprint(response)
except Exception as e:
    print(f"连接到 Flickr 时出错: {e}")


Flickr API 连接成功！
{'api_auth_is_oauth': {'_content': '1'},
 'api_key': {'_content': '9348c02df6636b4aacdbddf3b0a15233'},
 'api_sig': {'_content': 'dlaUjHcQXy9jEGP1yhblMglPBxY='},
 'auth_token': {'_content': ''},
 'format': {'_content': 'json'},
 'method': {'_content': 'flickr.test.echo'},
 'nojsoncallback': {'_content': '1'},
 'oauth_consumer_key': {'_content': '9348c02df6636b4aacdbddf3b0a15233'},
 'oauth_nonce': {'_content': '89033615453437165811737857964'},
 'oauth_signature': {'_content': 'dlaUjHcQXy9jEGP1yhblMglPBxY='},
 'oauth_signature_method': {'_content': 'HMAC-SHA1'},
 'oauth_timestamp': {'_content': '1737857964'},
 'oauth_version': {'_content': '1.0'},
 'stat': 'ok'}


In [6]:
import flickrapi
import pandas as pd
import pprint
import folium


#connect to flickr
flickr = flickrapi.FlickrAPI(api_key, api_secret, format='parsed-json')

### Define search location and display map

In [29]:
# Define the location (latitude and longitude) and search parameters
centre_latitude = 51.52320885442533 
centre_longitude = -0.004994936813072348 

# Define the bounding box. Use Open Street Map to get the coordinates
lat_north = 51.52626
lat_south = 51.50810
long_west = -0.01013
long_east = 0.00867

# Define the number of photos to retrieve per page
per_page = 250

# Create a map centered on the location
map_london = folium.Map(
    location=[centre_latitude, centre_longitude],
    tiles="Cartodb dark_matter",
    zoom_start=16,
    control_scale=True,
    zoom_control=False,
    dragging=False,
    scrollWheelZoom=False
)

# Add a circle marker to the map
folium.CircleMarker(
    location=[centre_latitude, centre_longitude],
    radius=2,
    color="cornflowerblue",
    stroke=False,
    fill=True,
    fill_opacity=0.6,
    opacity=1,
    # popup="{} pixels".format(radius),    
).add_to(map_london) 

# Add a rectangle to the map
folium.Rectangle(
    bounds=[[lat_north , long_west], [lat_south, long_east]],
    fill=True,
    fill_opacity=0.1,
    weight=1,
    color="cornflowerblue",  
).add_to(map_london)

# you can also save the map as html
# map_london.save("map_london.html")

map_london

The main command will be `flickr.photos.search` , please read the [documentation](https://www.flickr.com/services/api/flickr.photos.search.html) well. We will search the flickr photos that are inside the rectangle. 

In [30]:
# Define the bounding box coordinates (latitude and longitude)
# Format: bbox = "min_longitude,min_latitude,max_longitude,max_latitude"
bbox = str(long_west)+','+str(lat_south)+','+str(long_east)+','+str(lat_north)

# Search for photos in the bounding box
photos = flickr.photos.search(bbox=bbox, 
                              per_page=per_page, 
                              page=1,
                              has_geo=1, 
                              extras='geo,description,tags,views,media,url_n,date_taken,owner_name')
# Print the results
pprint.pprint(photos, compact=True)


{'photos': {'page': 1,
            'pages': 45,
            'perpage': 250,
            'photo': [{'accuracy': '16',
                       'context': 0,
                       'datetaken': '2025-01-04 13:00:38',
                       'datetakengranularity': 0,
                       'datetakenunknown': '0',
                       'description': {'_content': ''},
                       'farm': 66,
                       'geo_is_contact': 0,
                       'geo_is_family': 0,
                       'geo_is_friend': 0,
                       'geo_is_public': 1,
                       'height_n': 320,
                       'id': '54285707636',
                       'isfamily': 0,
                       'isfriend': 0,
                       'ispublic': 1,
                       'latitude': '51.513925',
                       'longitude': '0.008052',
                       'media': 'photo',
                       'media_status': 'ready',
                       'owner': '49428112@

Currently, we face two issues:  
- The response displays the results per page, in our case we can increase to a maximum of 250 results per page, but we still have more than one page.   
- The response data needs to be transformed into a table.  

The suggested solution involves the following steps:  

1. Determine the total number of pages.  
2. Retrieve each page sequentially.  
3. For every page retrieved, append the relevant content to a new table.  

### Determine the number of pages

Determine the number of pages, extact the results of the first entry.

In [31]:
photos = flickr.photos.search(bbox=bbox, 
                              per_page=per_page, 
                              page=1,
                              has_geo=1, 
                              extras='geo,description,tags,views,media,url_o,url_s,date_taken,owner_name')

total_pages = photos['photos']['pages']
total_photos = photos['photos']['total']

print(f"Total photos: {total_photos}")
print(f"Total pages: {total_pages}")
print("First entry:")
print("ID: " + photos['photos']['photo'][0]["id"])
print("Title: " + photos['photos']['photo'][0]["title"])
print("Owner: " + photos['photos']['photo'][0]["owner"])
print("Secret: " + photos['photos']['photo'][0]["secret"])
print("Server: " + photos['photos']['photo'][0]["server"])


Total photos: 11259
Total pages: 46
First entry:
ID: 54285707636
Title: IMG_6720
Owner: 49428112@N00
Secret: 62d3e7e812
Server: 65535


### Extract Page Information

Now, the code below is a function that takes a page, extracts the information and returns a dataframe:

In [32]:
def get_page(bbox, page, per_page):
    response = flickr.photos.search(
        bbox=bbox,
        per_page=per_page,
        page=page,
        has_geo=1,
        extras="geo,description,tags,views,media,url_s,date_taken,owner_name",
    )
    photos = response["photos"]["photo"]
    rows = []
    for photo in photos:
        new_row = {
            "id": photo["id"],
            "server": photo["server"],
            "secret": photo["secret"],
            "title": photo["title"],
            "tags": photo["tags"],
            "views": photo["views"],
            "description": photo["description"]["_content"],
            "date_taken": photo["datetaken"],
            "latitude": photo["latitude"],
            "longitude": photo["longitude"],
            "url_s": photo["url_s"],
            "owner": photo["owner"],
            "owner_name": photo["ownername"],
            "media": photo["media"],
        }
        rows.append(new_row)
    df = pd.DataFrame(
        rows,
        columns=[
            "id",
            "server",
            "secret",
            "title",
            "tags",
            "views",
            "description",
            "date_taken",
            "latitude",
            "longitude",
            "url_s",
            "owner_name",
            "owner",
            "media",
        ],
    )
    return df


get_page(bbox, 1, per_page)

id server      secret                                    title  \
0    54285707636  65535  62d3e7e812                                 IMG_6720   
1    54284819927  65535  fc49a9bb17                                 IMG_6719   
2    54285401483  65535  8cc9ca4614                                 IMG_6309   
3    54285396274  65535  ac0a352e4a                                 IMG_6310   
4    54285341940  65535  5c1d5e2927                                 IMG_6112   
..           ...    ...         ...                                      ...   
245  53769040850  65535  0698a2475c                                 Overpass   
246  53768620296  65535  e54179ff8e                  Mixers and the O2 Arena   
247  53765119795  65535  d6caba285c  EMC5 LK15FKE Optare Metrocity EV MC1080   
248  53764703766  65535  de4af10d5b       Rears of 143 F143PHM & 218 S218LLO   
249  53765116695  65535  b31d8aab2c                    T792 HLX492 AEC Regal   

                                            tags views description  \
0                                                    0               
1                                                    3               
2                                                    0               
3                                                    0               
4                                                    0               
..                                           ...   ...         ...   
245  london towerhamlets gentrification graffiti    31               
246   london towerhamlets concretemixers o2arena    17               
247                                                 70               
248                                                143               
249                                                 76               

              date_taken   latitude longitude  \
0    2025-01-04 13:00:38  51.513925  0.008052   
1    2025-01-04 13:00:33  51.513886  0.007958   
2    2024-12-10 17:41:47  51.513741  0.008080   
3    2024-12-10 17:42:10  51.513716  0.008244   
4    2024-11-20 18:03:21  51.513797  0.008202   
..                   ...        ...       ...   
245  2024-03-16 15:07:57  51.510044  0.004280   
246  2024-03-16 15:08:09  51.508582  0.005986   
247  2016-07-23 11:26:37  51.523527  0.002933   
248  2016-07-23 11:18:40  51.523061  0.003052   
249  2016-07-23 11:12:14  51.523194  0.003038   

                                                 url_s  \
0    https://live.staticflickr.com/65535/5428570763...   
1    https://live.staticflickr.com/65535/5428481992...   
2    https://live.staticflickr.com/65535/5428540148...   
3    https://live.staticflickr.com/65535/5428539627...   
4    https://live.staticflickr.com/65535/5428534194...   
..                                                 ...   
245  https://live.staticflickr.com/65535/5376904085...   
246  https://live.staticflickr.com/65535/5376862029...   
247  https://live.staticflickr.com/65535/5376511979...   
248  https://live.staticflickr.com/65535/5376470376...   
249  https://live.staticflickr.com/65535/5376511669...   

                   owner_name         owner  media  
0    Ian K Tindale (u0421793)  49428112@N00  photo  
1    Ian K Tindale (u0421793)  49428112@N00  photo  
2    Ian K Tindale (u0421793)  49428112@N00  photo  
3    Ian K Tindale (u0421793)  49428112@N00  photo  
4    Ian K Tindale (u0421793)  49428112@N00  photo  
..                        ...           ...    ...  
245               Loz Flowers  99245765@N00  photo  
246               Loz Flowers  99245765@N00  photo  
247                    vjaska  50835692@N05  photo  
248                    vjaska  50835692@N05  photo  
249                    vjaska  50835692@N05  photo  

[250 rows x 14 columns]

### Go through all pages
The next step involves creating a loop that processes all the pages and consolidates the data into a single large dataframe. Since each request takes approximately 5 to 6 seconds, processing all 299 pages could take around 30 minutes. While this duration is manageable, there are potential risks during such a lengthy process.

Here are a few considerations to address these challenges:
- **Download in batches**: For instance, process 20 pages at a time. However, this may not be an ideal solution.
- **Use a smaller bounding box**: This approach is more effective.

In the example provided below, only the first 20 pages are downloaded. To process all pages, replace the relevant line with `for page in range(1, total_pages + 1):`.

In [40]:
df = pd.DataFrame()

for page in range(1, 30):
    new_df = get_page(bbox, page, per_page)
    print(f"Getting page {page} of {total_pages}")
    df = pd.concat([df, new_df], ignore_index=True)
    print(f"Total photos so far: {len(df)}")


df

Getting page 1 of 46
Total photos so far: 250
Getting page 2 of 46
Total photos so far: 500
Getting page 3 of 46
Total photos so far: 750
Getting page 4 of 46
Total photos so far: 1000
Getting page 5 of 46
Total photos so far: 1250
Getting page 6 of 46
Total photos so far: 1500
Getting page 7 of 46
Total photos so far: 1750
Getting page 8 of 46
Total photos so far: 2000
Getting page 9 of 46
Total photos so far: 2250
Getting page 10 of 46
Total photos so far: 2500
Getting page 11 of 46
Total photos so far: 2750
Getting page 12 of 46
Total photos so far: 3000
Getting page 13 of 46
Total photos so far: 3250
Getting page 14 of 46
Total photos so far: 3500
Getting page 15 of 46
Total photos so far: 3750
Getting page 16 of 46
Total photos so far: 4000
Getting page 17 of 46
Total photos so far: 4250
Getting page 18 of 46
Total photos so far: 4500
Getting page 19 of 46
Total photos so far: 4750
Getting page 20 of 46
Total photos so far: 5000
Getting page 21 of 46
Total photos so far: 5250
Gett

id server      secret     title  \
0     54285707636  65535  62d3e7e812  IMG_6720   
1     54284819927  65535  fc49a9bb17  IMG_6719   
2     54285401483  65535  8cc9ca4614  IMG_6309   
3     54285396274  65535  ac0a352e4a  IMG_6310   
4     54285341940  65535  5c1d5e2927  IMG_6112   
...           ...    ...         ...       ...   
7245  53804079912  65535  eafeed2a36     WORKS   
7246  53794455667  65535  48dbd98eea             
7247  53794451577  65535  8bc3b95887             
7248  53795708254  65535  61987b1fb1             
7249  53795391566  65535  1d1e6d6630             

                                                   tags views description  \
0                                                           0               
1                                                           3               
2                                                           0               
3                                                           0               
4                                                           0               
...                                                 ...   ...         ...   
7245  olympusep1 ttartisan25mmf20 building word outs...   184               
7246                                                        8               
7247                                                        7               
7248                                                        7               
7249                                                        7               

               date_taken   latitude  longitude  \
0     2025-01-04 13:00:38  51.513925   0.008052   
1     2025-01-04 13:00:33  51.513886   0.007958   
2     2024-12-10 17:41:47  51.513741   0.008080   
3     2024-12-10 17:42:10  51.513716   0.008244   
4     2024-11-20 18:03:21  51.513797   0.008202   
...                   ...        ...        ...   
7245  2024-05-11 19:51:19  51.509468   0.004881   
7246  2024-06-16 10:48:05  51.517588   0.004950   
7247  2024-06-16 10:38:50  51.522888  -0.007012   
7248  2024-06-16 10:36:19  51.523388  -0.004653   
7249  2024-06-16 10:41:29  51.519169  -0.006573   

                                                  url_s  \
0     https://live.staticflickr.com/65535/5428570763...   
1     https://live.staticflickr.com/65535/5428481992...   
2     https://live.staticflickr.com/65535/5428540148...   
3     https://live.staticflickr.com/65535/5428539627...   
4     https://live.staticflickr.com/65535/5428534194...   
...                                                 ...   
7245  https://live.staticflickr.com/65535/5380407991...   
7246  https://live.staticflickr.com/65535/5379445566...   
7247  https://live.staticflickr.com/65535/5379445157...   
7248  https://live.staticflickr.com/65535/5379570825...   
7249  https://live.staticflickr.com/65535/5379539156...   

                    owner_name         owner  media  
0     Ian K Tindale (u0421793)  49428112@N00  photo  
1     Ian K Tindale (u0421793)  49428112@N00  photo  
2     Ian K Tindale (u0421793)  49428112@N00  photo  
3     Ian K Tindale (u0421793)  49428112@N00  photo  
4     Ian K Tindale (u0421793)  49428112@N00  photo  
...                        ...           ...    ...  
7245                    sarble  32014910@N00  photo  
7246          Robin Stephenson   8798439@N03  photo  
7247          Robin Stephenson   8798439@N03  photo  
7248          Robin Stephenson   8798439@N03  photo  
7249          Robin Stephenson   8798439@N03  photo  

[7250 rows x 14 columns]

and we save the dataframe....

In [41]:
df.to_csv(r"E:\ucl\MyPythonModules\london_photos.csv", index=False)

### Map Display
We display the location of our points on the map: 

In [50]:
import folium

# Create a map centered on the location
map_london = folium.Map(
    location=[centre_latitude, centre_longitude],
    tiles="CartoDB Positron",  # CartoDB Positron is without labels
    zoom_start=16,
    control_scale=True,
    zoom_control=False,
    dragging=False,
    scrollWheelZoom=False
)

# Add a circle marker to the map
folium.CircleMarker(
    location=[centre_latitude, centre_longitude],
    radius=2,
    color="cornflowerblue",
    stroke=False,
    fill=True,
    fill_opacity=0.6,
    opacity=1,
).add_to(map_london)

# Add a rectangle to the map
folium.Rectangle(
    bounds=[[lat_north, long_west], [lat_south, long_east]],
    fill=True,
    fill_opacity=0.05,
    weight=.5,
    color="cornflowerblue",
).add_to(map_london)

# Add a circle marker for each photo
latitudes = df['latitude']
longitudes = df['longitude']

for latitude, longitude in zip(latitudes, longitudes):
    coordinate = [latitude, longitude]
    radius = 1
    folium.CircleMarker(
        location=coordinate,
        radius=radius,
        stroke=False,
        fill=True,
        fillColor="orchid",
        fill_opacity=0.3,
        opacity=0.3,
    ).add_to(map_london)

# Display the map
map_london


**Colors**  

Ever wondered where color names like "orchid" or "cornflowerblue" come from? These are built-in Windows colors, and you can find the complete list [here](https://learn.microsoft.com/en-us/dotnet/api/system.windows.media.colors?view=windowsdesktop-9.0).

---

## Combined Script

This is the combined script: 

### Import Libaries

In [115]:
import sys

sys.path.append(r"C:\Users\vince\Dropbox\Codes\passwords")

import passwords as pw
import flickrapi
import pandas as pd
import pprint
import folium

api_key = pw.flickr_key
api_secret = pw.flickr_secret

# connect to flickr
flickr = flickrapi.FlickrAPI(api_key, api_secret, format="parsed-json")

### Set search parameters

In [126]:
# Define the location (latitude and longitude) and search parameters
centre_latitude = 51.51239
centre_longitude = 0.00496

# Define the bounding box. Use Open Street Map to get the coordinates
lat_north = 51.51550
lat_south = 51.50941
long_west = 0.00024
long_east = 0.01015

# Format: bbox = "min_longitude,min_latitude,max_longitude,max_latitude" for Flickr search
bbox = str(long_west)+','+str(lat_south)+','+str(long_east)+','+str(lat_north)

# Define the number of photos to retrieve per page
per_page = 250

# Create a map centered on the location
map_london = folium.Map(
    location=[centre_latitude, centre_longitude],
    tiles="Cartodb dark_matter",
    zoom_start=16,
    control_scale=True,
    zoom_control=False,
    dragging=False,
    scrollWheelZoom=False,
)

# Add a circle marker to the map
folium.CircleMarker(
    location=[centre_latitude, centre_longitude],
    radius=2,
    color="cornflowerblue",
    stroke=False,
    fill=True,
    fill_opacity=0.6,
    opacity=1,
    popup="{} pixels".format(radius),
).add_to(map_london)

# Add a rectangle to the map
folium.Rectangle(
    bounds=[[lat_north, long_west], [lat_south, long_east]],
    fill=True,
    fill_opacity=0.1,
    weight=1,
    color="cornflowerblue",
).add_to(map_london)

map_london

### Get amount of pages and photos

In [127]:
photos = flickr.photos.search(bbox=bbox, per_page=per_page, page=1, has_geo=1)

total_pages = photos["photos"]["pages"]
total_photos = photos["photos"]["total"]

print(f"Total photos: {total_photos}")
print(f"Total pages: {total_pages}")

Total photos: 3841
Total pages: 16


### Extract information

In [128]:
def get_page(bbox, page, per_page):
    response = flickr.photos.search(
        bbox=bbox,
        per_page=per_page,
        page=page,
        has_geo=1,
        extras="geo,description,tags,views,media,url_s,date_taken,owner_name",
    )
    photos = response["photos"]["photo"]
    rows = []
    for photo in photos:
        new_row = {
            "id": photo["id"],
            "server": photo["server"],
            "secret": photo["secret"],
            "title": photo["title"],
            "tags": photo["tags"],
            "views": photo["views"],
            "description": photo["description"]["_content"],
            "date_taken": photo["datetaken"],
            "latitude": photo["latitude"],
            "longitude": photo["longitude"],
            "url_s": photo["url_s"],
            "owner": photo["owner"],
            "owner_name": photo["ownername"],
            "media": photo["media"],
        }
        rows.append(new_row)
    df = pd.DataFrame(
        rows,
        columns=[
            "id",
            "server",
            "secret",
            "title",
            "tags",
            "views",
            "description",
            "date_taken",
            "latitude",
            "longitude",
            "url_s",
            "owner_name",
            "owner",
            "media",
        ],
    )
    return df


df = pd.DataFrame()

# Use this code to get only the first 10 pages of photos
for page in range(1, 10):
    new_df = get_page(bbox, page, per_page)
    print(f"Getting page {page} of {total_pages}")
    df = pd.concat([df, new_df], ignore_index=True)
    print(f"Total photos so far: {len(df)}")

""" 
Use this code to get all the photos in the bounding box: 
for page in range(1, total_pages + 1):
    new_df = get_page(bbox, page, per_page)
    print(f"Getting page {page} of {total_pages}")
    df = pd.concat([df, new_df], ignore_index=True)
    print(f"Total photos so far: {len(df)}") 
"""

df.to_csv("london_photos.csv", index=False)

df

Getting page 1 of 16
Total photos so far: 250
Getting page 2 of 16
Total photos so far: 500
Getting page 3 of 16
Total photos so far: 750
Getting page 4 of 16
Total photos so far: 1000
Getting page 5 of 16
Total photos so far: 1250
Getting page 6 of 16
Total photos so far: 1500
Getting page 7 of 16
Total photos so far: 1750
Getting page 8 of 16
Total photos so far: 2000
Getting page 9 of 16
Total photos so far: 2250


id server      secret  \
0     54188656132  65535  9eb07f8473   
1     54188288630  65535  1e94c66157   
2     54186949737  65535  fbf67379c4   
3     54188115424  65535  6b76e2d37b   
4     54186949517  65535  a17c975acf   
...           ...    ...         ...   
2245  19669717713    270  d30ac971ea   
2246  20261193506    459  b17fea2926   
2247  20276112171   3788  146972c94d   
2248  19644544533   3774  b8596fbdbc   
2249  20265412805    362  ed8c0febaa   

                                                  title  \
0                                  Go-Ahead London MHV6   
1           EastLondon-37556-YX60DXO-CanningTown-300124   
2           EastLondon-47992-YJ12GVR-CanningTown-300124   
3           EastLondon-64202-LF20XKP-CanningTown-300124   
4           EastLondon-47985-YJ60PFE-CanningTown-300124   
...                                                 ...   
2245                         City Island, Orchard Place   
2246  Stagecoach London 19795 on route 5 at Canning ...   
2247                                        City Island   
2248                                        City Island   
2249                         DLR on the Limmo Peninsula   

                                                   tags views  \
0     goahead london mhv6 bu16oyo volvo b5lh mcv evo...   485   
1     yx60dxo enviro200 firstcapital dm44169 route30...   433   
2     yj12gvr ctplus optaresolo optare solo route309...   470   
3     lf20xkp bydd8ur route323 eastlondonbus canning...   400   
4     yj60pfe ctplus optaresolo optare solo route309...   309   
...                                                 ...   ...   
2245  roundtower towerhamlets trinitybuoywharf round...   892   
2246  bus transport publictransport stagecoach londo...  2204   
2247                roundtower towerhamlets roundtower2  1237   
2248                roundtower towerhamlets roundtower2  1081   
2249                roundtower towerhamlets roundtower2  1131   

                                            description           date_taken  \
0     Go-Ahead London MHV6 (BU16 OYO)\nVolvo B5LH/MC...  2024-12-07 13:17:20   
1     East London 37556 (YX60 DXO) \n\nADL Enviro 20...  2024-01-30 00:00:00   
2     East London 47992 (YJ12 GVR) \n\nFormer CT Plu...  2024-01-30 00:00:03   
3     East London 64202 (LF20 XKP) \n\nBYD D8UR / AD...  2024-01-30 00:00:02   
4     East London 47985 (YJ60 PFE) \n\nFormer CT Plu...  2024-01-30 00:00:01   
...                                                 ...                  ...   
2245  Thousands of private residents will be driving...  2015-07-11 11:03:51   
2246  This is the closest route 5 gets to Central Lo...  2015-08-03 13:57:59   
2247  One day this red footbridge will be a new way ...  2015-08-02 13:49:56   
2248  Former industrial peninsula, soon to be luxury...  2015-08-02 13:48:49   
2249  In the background, the first fruits of the Cit...  2015-08-02 13:58:31   

       latitude longitude                                              url_s  \
0     51.514731  0.007992  https://live.staticflickr.com/65535/5418865613...   
1     51.514291  0.008368  https://live.staticflickr.com/65535/5418828863...   
2     51.514291  0.008368  https://live.staticflickr.com/65535/5418694973...   
3     51.514291  0.008368  https://live.staticflickr.com/65535/5418811542...   
4     51.514291  0.008368  https://live.staticflickr.com/65535/5418694951...   
...         ...       ...                                                ...   
2245  51.510772  0.005171  https://live.staticflickr.com/270/19669717713_...   
2246  51.515259  0.007756  https://live.staticflickr.com/459/20261193506_...   
2247  51.513363  0.005578  https://live.staticflickr.com/3788/20276112171...   
2248  51.513363  0.005578  https://live.staticflickr.com/3774/19644544533...   
2249  51.513162  0.003883  https://live.staticflickr.com/362/20265412805_...   

          owner_name            owner  media  
0        gbenviro200     33732381@N04  photo  
1     Michael Wadman     330

### Map display

In [130]:
# Create a map centered on the location
map_london = folium.Map(
    location=[centre_latitude, centre_longitude],
    tiles="Cartodb dark_matter",
    zoom_start=16,
    control_scale=True,
    zoom_control=False,
    dragging=False,
    scrollWheelZoom=False
)

# Add a circle marker to the map
folium.CircleMarker(
    location=[centre_latitude, centre_longitude],
    radius=2,
    color="cornflowerblue",
    stroke=False,
    fill=True,
    fill_opacity=0.6,
    opacity=1,
    popup="{} pixels".format(radius),    
).add_to(map_london) 

# Add a rectangle to the map
folium.Rectangle(
    bounds=[[lat_north , long_west], [lat_south, long_east]],
    fill=True,
    fill_opacity=0.05,
    weight=.5,
    color="cornflowerblue",  
).add_to(map_london)

# Add a circle marker for each photo
latitudes = df['latitude']
longitudes = df['longitude']

for latitude, longitude in  zip(latitudes,longitudes):
  coordinate = [latitude,longitude]
  radius = 1
  folium.CircleMarker(
    location=coordinate,
    radius=radius,
    stroke=False,
    fill=True,
    fillColor="orchid", 
    fill_opacity=0.3,
    opacity=0.3,
  ).add_to(map_london)
  
map_london

## What's Next?  

If you examine this [Flickr Image](https://www.flickr.com/photos/33075566@N08/54187832141), you'll notice additional information associated with the image, such as "Favorites" or "Comments," which were not captured during the initial search.  
To address this, you'll need to iterate through the list and include the missing entries. Refer to the documentation to determine the appropriate API calls required to retrieve this data.

You can also convert the image's capture date into a datetime object, which helps you better analyze and understand the time aspect.